# Setting

In [1]:
import os
import torch
import logging
import json
import shutil
from ultralytics import YOLO
from PIL import Image, ImageDraw

In [2]:
import random
random.seed(42)  # 시드 설정

obc_list = ['apple', 'banana','bowl','dumbbell']  

In [3]:
# log 생성
logger = logging.getLogger()
logger.setLevel(logging.INFO) 
formatter = logging.Formatter('Time : %(asctime)s , Message : %(message)s')   # log 출력 형식 지정

# log를 console에 출력하도록 설정
stream_handler = logging.StreamHandler()
stream_handler.setFormatter(formatter)
logger.addHandler(stream_handler)

In [4]:
# device 선택
# GPU 사용 불가능할 경우 CPU를 활용함
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')   # ★★★★★
logger.info(f'using {device}')

Time : 2024-03-06 10:39:38,535 , Message : using cuda:0


# Train

In [5]:
# 모델 다운로드
model = YOLO(model='yolov8s.pt')   
logger.info('Model downloaded')

# 모델을 device로 이동
model.to(device)  
logger.info(f'Model move to {device} completed')

100%|██████████| 21.5M/21.5M [00:01<00:00, 20.5MB/s]
Time : 2024-03-05 11:30:32,804 , Message : Model downloaded
Time : 2024-03-05 11:30:32,927 , Message : Model move to cuda:0 completed


In [7]:
logger.info('Train started')

# 모델 학습
'''
epochs : 학습 반복 횟수
batch : 한 번에 학습하는 데이터 개수
workers : CPU 병렬 작업 개수
'''
model.train(data='C:/Users/njh26/Desktop/Coding/03.Project/Object_Detection_Yolov8/subset_data_TVT/Yolov8_data.yaml',        # 절대경로 입력  # ★★★★★
            epochs=10, batch=8, workers=4)     # cpu에서 구동시 workers = 0로 변경     # ★★★★★
logger.info('Train ended')

Time : 2024-03-05 11:45:33,053 , Message : Train started
New https://pypi.org/project/ultralytics/8.1.23 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.0.145  Python-3.8.6 torch-2.2.0+cu118 CUDA:0 (NVIDIA GeForce RTX 4060, 8187MiB)
engine\trainer: task=detect, mode=train, model=yolov8s.pt, data=C:/Users/njh26/Desktop/Coding/03.Project/Object_Detection_Yolov8/subset_data_TVT/Yolov8_data.yaml, epochs=10, patience=50, batch=8, imgsz=640, save=True, save_period=-1, cache=False, device=None, workers=4, project=None, name=None, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, show=False, save_txt=False, save_conf=False, save_crop=Fals

# Validation

In [8]:
logger.info('Validation started')

# 모델 검증
model.val()

logger.info('Validation ended')

Time : 2024-03-05 13:15:24,515 , Message : Validation started
Ultralytics YOLOv8.0.145  Python-3.8.6 torch-2.2.0+cu118 CUDA:0 (NVIDIA GeForce RTX 4060, 8187MiB)
Model summary (fused): 168 layers, 11127132 parameters, 0 gradients
val: Scanning C:\Users\njh26\Desktop\Coding\03.Project\Object_Detection_Yolov8\subset_data_TVT\valid\labels\apple.cache... 4411 images, 0 backgrounds, 0 corrupt: 100%|██████████| 4411/4411 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 552/552 [00:48<00:00, 11.42it/s]
                   all       4411       7033      0.922      0.909      0.948      0.924
                 apple       4411       1075      0.935      0.941      0.972      0.961
                banana       4411       2182      0.966      0.962      0.987      0.955
                  bowl       4411       1152      0.858      0.821      0.864      0.837
              dumbbell       4411       2624       0.93       0.91   

In [5]:
# 학습 완료된 모델 로드
model = YOLO(model='./runs/detect/train/weights/best.pt')  # 모델 파일 경로 입력  # ★★★★★
logger.info('Train Completed Model loaded') 

# 모델을 device로 이동
model.to(device)  
logger.info(f'Model move to {device} completed')

Time : 2024-03-06 10:39:44,229 , Message : Train Completed Model loaded
Time : 2024-03-06 10:39:44,384 , Message : Model move to cuda:0 completed


# Validation of Test Data

In [23]:
logger.info("Validation of Test Data started")

# Test Data에 대한 검증 수행
# Confusion Matrix / class별 mAP 계산
model.val(data='C:/Users/njh26/Desktop/Coding/03.Project/Object_Detection_Yolov8/subset_data_TVT/Yolov8_data.yaml',    # yaml 파일의 절대경로 입력 필요  # ★★★★★
          split = 'test', imgsz = 640, device = device)

# 폴더명 변경
# 자동으로 생성되는 폴더명에서 알아보기 쉽도록 변경
os.rename('./runs/detect/val2', f'./runs/detect/predict_val')

logger.info("Validation of Test Data completed")

Time : 2024-03-05 14:25:14,715 , Message : Validation of Test Data started
Time : 2024-03-05 14:25:14,715 , Message : Validation of Test Data started
Ultralytics YOLOv8.0.145  Python-3.8.6 torch-2.2.0+cu118 CUDA:0 (NVIDIA GeForce RTX 4060, 8187MiB)
Model summary (fused): 168 layers, 11127132 parameters, 0 gradients
val: Scanning C:\Users\njh26\Desktop\Coding\03.Project\Object_Detection_Yolov8\subset_data_TVT\test\labels\apple.cache... 4413 images, 0 backgrounds, 0 corrupt: 100%|██████████| 4413/4413 [00:00<?, ?it/s]
val: WARNING  C:\Users\njh26\Desktop\Coding\03.Project\Object_Detection_Yolov8\subset_data_TVT\test\images\bowl\IMG_3346768_bowl(bowl).jpg: 1 duplicate labels removed
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 276/276 [00:44<00:00,  6.16it/s]
                   all       4413       7044      0.921      0.918      0.957      0.934
                 apple       4413       1033      0.935      0.948      0.972     

# Predict

In [24]:
# 목표로 했던 이미지 테스트
test_image_path = r'C:\Users\njh26\Desktop\Coding\03.Project\Object_Detection_Yolov8\IMG_0058403_apple(apple).jpg'
model.predict(test_image_path, stream = False, save = True, imgsz=640, device = device)

# 폴더명 변경
try : 
    os.rename('./runs/detect/predict', 
            f'./runs/detect/pred_one_image')  
except : 
    print('Folder has been converted')


image 1/1 C:\Users\njh26\Desktop\Coding\03.Project\Object_Detection_Yolov8\IMG_0058403_apple(apple).jpg: 640x384 1 apple, 1 banana, 1 dumbbell, 38.0ms
Speed: 2.0ms preprocess, 38.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 384)
Results saved to runs\detect\predict


In [25]:
logger.info('Test started')

# Test 이미지 파일의 경로
test_path = 'C:/Users/njh26/Desktop/Coding/03.Project/Object_Detection_Yolov8/subset_data_TVT/test/{}/{}'   # 절대경로 입력 필요   # ★★★★★  

for obc in obc_list: 
        # 파일명 리스트 가져오기
        test_image_list = os.listdir(test_path.format('images', obc))
        test_label_list = os.listdir(test_path.format('labels', obc))

        # 파일 경로 리스트 가져오기
        test_image_path_list = [os.path.join(test_path.format('images', obc), file_name) for file_name in test_image_list]
        test_label_path_list = [os.path.join(test_path.format('labels', obc), file_name) for file_name in test_label_list]

        # 테스트 이미지와 라벨 가져오기
        for test_image, test_label in zip(test_image_path_list, test_label_path_list):

            cls_origins = []  # 정답 클래스를 담을 리스트
            
            # 정답 값 불러오기
            with open(test_label, 'r', encoding = 'utf-8') as txt:
                lines = txt.readlines()
                for line in lines:
                    parts = line.split()
                    class_label = int(parts[0])
                    cls_origins.append(class_label)

            # 개별 이미지 파일의 BBOX 예측
            results = model.predict(test_image, stream = False, save = True, imgsz=640, device = device)
            
            # 예측 결과
            for result in results:
                # 파일명
                file_name = result.path.split('\\')[-1] 
                
                # 예측 결과 클래스
                cls = result.boxes.cls
                cls_predicts = list(map(int, cls.tolist()))  # 리스트로 변경

                # 예측 신뢰도
                confidence = result.boxes.conf

                # 예측 클래스와 실제 클래스 비교하여 True, False 생성
                cls_result = [cls_origin == cls_predict for cls_origin, cls_predict in zip(cls_origins, cls_predicts)]

                logger.info(f"\n" +
                            f"파일명 : {file_name} \n" +
                            f"실제 클래스 : {cls_origins} \n" + 
                            f"예측 클래스 : {cls_predicts} \n" + 
                            f"예측 신뢰도 : {confidence.tolist()} \n" + 
                            f"예측 결과 : {cls_result}")

        # 폴더명 변경
        try : 
            os.rename('./runs/detect/predict', 
                    f'./runs/detect/pred_{obc}')  
        except : 
            print('Folder has been converted')
        
        logger.info(f'{obc}-{len(os.listdir(test_path.format("images", obc)))} test ended')
logger.info('Test ended')

Time : 2024-03-05 14:26:35,725 , Message : Test started
Time : 2024-03-05 14:26:35,725 , Message : Test started

image 1/1 C:\Users\njh26\Desktop\Coding\03.Project\Object_Detection_Yolov8\subset_data_TVT\test\images\apple\IMG_0129218_apple(apple).jpg: 384x640 2 apples, 61.0ms
Speed: 4.0ms preprocess, 61.0ms inference, 5.0ms postprocess per image at shape (1, 3, 384, 640)
Results saved to runs\detect\predict
Time : 2024-03-05 14:26:35,859 , Message : 
파일명 : IMG_0129218_apple(apple).jpg 
실제 클래스 : [0, 0] 
예측 클래스 : [0, 0] 
예측 신뢰도 : [0.9776831269264221, 0.9710635542869568] 
예측 결과 : [True, True]
Time : 2024-03-05 14:26:35,859 , Message : 
파일명 : IMG_0129218_apple(apple).jpg 
실제 클래스 : [0, 0] 
예측 클래스 : [0, 0] 
예측 신뢰도 : [0.9776831269264221, 0.9710635542869568] 
예측 결과 : [True, True]

image 1/1 C:\Users\njh26\Desktop\Coding\03.Project\Object_Detection_Yolov8\subset_data_TVT\test\images\apple\IMG_0129225_apple(apple).jpg: 384x640 2 apples, 45.0ms
Speed: 2.0ms preprocess, 45.0ms inference, 3.0ms pos

# Ground Truth and Predicted Box by Yolov8

In [6]:
# 폴더 생성
dir = './runs/detect/GT_on_pred_{}/'

for obc in obc_list: 
        try:
            if not os.path.exists(dir.format(obc)):
                os.makedirs(dir.format(obc))
            else:
                print('Folder has already been created')
        except OSError:
            print('Error: Creating folder. ')

logger.info('Folder created')

Time : 2024-03-06 10:39:53,650 , Message : Folder created


In [7]:
logger.info('Draw GT on Predicted Image started')

# 예측 이미지 파일의 경로
pred_path = './runs/detect/pred_{}/'             

# Test 파일의 경로
test_path = './subset_data_TVT/test/{}/{}/'   

# 저장될 경로
save_path = './runs/detect/GT_on_pred_{}/'         

# 종별, 상태별 예측 이미지 위에 GT 그리기
for obc in obc_list:   

        # 이미지 파일명 리스트 저장
        predicted_images = os.listdir(pred_path.format(obc))

        for image in predicted_images:
            # 이미지 열기
            img = Image.open(pred_path.format(obc) + image)
            draw = ImageDraw.Draw(img)

            # 라벨링 파일 가져오기
            with open(test_path.format('RS_labels', obc) + image.split('.')[0] + '_(4_1).json', mode = 'r', encoding = 'utf-8') as f:
                jsonfile = json.load(f)

            # Ground Truth 그리기
            for annot in jsonfile['annotations']:
                draw.rectangle((annot['bbox'][0], annot['bbox'][1],
                               annot['bbox'][0] + annot['bbox'][2], annot['bbox'][1] + annot['bbox'][3]),
                                outline='yellow',   
                                width=5)  

            # 이미지 저장 
            img.save(save_path.format(obc) + image)              

        logger.info(f'{obc}-{len(os.listdir(pred_path.format(obc)))} ended')
        
logger.info('Draw GT on Predicted Image ended')

Time : 2024-03-06 10:39:55,152 , Message : Draw GT on Predicted Image started
Time : 2024-03-06 10:40:06,659 , Message : apple-485 ended
Time : 2024-03-06 10:40:45,328 , Message : banana-1691 ended
Time : 2024-03-06 10:40:57,066 , Message : bowl-495 ended
Time : 2024-03-06 10:41:38,152 , Message : dumbbell-1742 ended
Time : 2024-03-06 10:41:38,153 , Message : Draw GT on Predicted Image ended


# Tensor Board

In [8]:
from torch.utils.tensorboard import SummaryWriter
import pandas as pd

In [9]:
# 학습 과정에서 발생한 loss 값 등 불러오기
Results = pd.read_csv('./runs/detect/train/results.csv')          

# 텐서보드용 데이터를 저장하는 폴더명 지정
Writer = SummaryWriter('./Tensorboard')                      

for k in range(len(Results)):
    # epoch별 loss 값 불러오기
    epoch = Results.iloc[k,0]
    box_loss = Results.iloc[k,1]
    cls_loss = Results.iloc[k,2]
    dfl_loss = Results.iloc[k,3]

    # 스칼라 추가
    Writer.add_scalar('train/box_loss', box_loss, epoch)
    Writer.add_scalar('train/cls_loss', cls_loss, epoch)
    Writer.add_scalar('train/dfl_loss', dfl_loss, epoch)

Writer.close()

In [10]:
%load_ext tensorboard

%tensorboard --logdir="C:/Users/njh26/Desktop/Coding/03.Project/Object_Detection_Yolov8/Tensorboard" --host localhost --port=8008      # ★★★★★
# 절대경로 입력 필요, 포트번호는 임의의 4자리 수로 입력 가능    # ★★★★★

logger.info('Tensorboard created')

'''
ERROR: Timed out waiting for TensorBoard to start  
주피터 노트북 실행시간 초과로 위 오류 발생시, 터미널에서 실행해야 함

1. 3가지 방법 중 하나로 가상환경에 접속
    #1 cmd로 접속 - 가상환경이 자동으로 접속되는 경우

    #2 cmd로 접속 - 가상환경이 자동으로 접속되지 않는 경우
    anaconda 내에 가상환경이 존재하는 경로를 직접 입력하여 접속
    경로/activate {가상환경명}
    ex) C:/ProgramData/anaconda3/Scripts/activate Edible_Insects   # ★★★★★

    #3 anaconda로 접속  
    anaconda navigator로 가상환경 선택하여 환경으로 접속  

2. 접속 이후 tensorboard --logdir="C:/Users/njh26/Desktop/Coding/03.Project/Object_Detection_Yolov8/Tensorboard" --host localhost --port=8008    # ★★★★★
(절대경로 입력 필요, 포트번호는 임의로 설정 가능하나 타 모델과 겹치지 않도록 설정)

터미널에 출력되는 http://localhost:8008/ 접속하여 확인
'''

ERROR: Timed out waiting for TensorBoard to start. It may still be running as pid 9324.

Time : 2024-03-06 10:43:24,338 , Message : Tensorboard created


'\nERROR: Timed out waiting for TensorBoard to start  \n주피터 노트북 실행시간 초과로 위 오류 발생시, 터미널에서 실행해야 함\n\n1. 3가지 방법 중 하나로 가상환경에 접속\n    #1 cmd로 접속 - 가상환경이 자동으로 접속되는 경우\n\n    #2 cmd로 접속 - 가상환경이 자동으로 접속되지 않는 경우\n    anaconda 내에 가상환경이 존재하는 경로를 직접 입력하여 접속\n    경로/activate {가상환경명}\n    ex) C:/ProgramData/anaconda3/Scripts/activate Edible_Insects   # ★★★★★\n\n    #3 anaconda로 접속  \n    anaconda navigator로 가상환경 선택하여 환경으로 접속  \n\n2. 접속 이후 tensorboard --logdir="C:/Users/njh26/Desktop/Coding/03.Project/Object_Detection_Yolov8/Tensorboard" --host localhost --port=8008    # ★★★★★\n(절대경로 입력 필요, 포트번호는 임의로 설정 가능하나 타 모델과 겹치지 않도록 설정)\n\n터미널에 출력되는 http://localhost:8008/ 접속하여 확인\n'